# Capstone Project: Finding a suitable location for Burger point in Puerto Rico (PR) state

#### Business Problem:

New entrepreneurs who want to start a restaurant business find it difficult to find a best suitable location where there are more potential customers to serve and earn profits.

Problem statement. Find the best location in Puerto Rico State, USA to start a Burger point.

This project analyse the neighbourhood of Puerto Rico and come up with the best location to start new Burger point


#### Data

Data for the analysis is taken from the below URL

https://zipcodedownload.com/lookup/Puerto_Rico

It has Zip code, City Name, State Name columns and links to find the latitude and longitude for each Zip code. I have pulled all these details and saved it in csv file 'PRZipcodes.csv' 


#### Importing Libraries and creating a DataFrame from the Wiki Data

In [3]:
import numpy as np 
import pandas as pd
import requests
from bs4 import BeautifulSoup

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

!conda install -c conda-forge geopy --yes
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes
#=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

# All requested packages already installed.

Solving environment: done

# All requested packages already installed.

Libraries imported.


#### Reading the Data from csv file. 
ZIP stored as number without leading zeros. Hence zeroes prefixed

In [4]:
df=pd.read_csv('PRZipcodes.csv')
df['ZIP']= df['ZIP'].astype(str)
df['ZIP'] = df['ZIP'].apply(lambda x: x.zfill(5))
df

ZIP        City Name    County Name   State Name        LAT        LNG
0    00601         Adjuntas       Adjuntas  Puerto Rico  18.165950 -66.723630
1    00602           Aguada         Aguada  Puerto Rico  18.361945 -67.175597
2    00603        Aguadilla      Aguadilla  Puerto Rico  18.455183 -67.119887
3    00604        Aguadilla      Aguadilla  Puerto Rico  18.505290 -67.135900
4    00605        Aguadilla      Aguadilla  Puerto Rico  18.436150 -67.151340
5    00606          Maricao        Maricao  Puerto Rico  18.158345 -66.932911
6    00610           Anasco         Anasco  Puerto Rico  18.295366 -67.125135
7    00611          Angeles         Utuado  Puerto Rico  18.287720 -66.797580
8    00612          Arecibo        Arecibo  Puerto Rico  18.402253 -66.711397
9    00613          Arecibo        Arecibo  Puerto Rico  18.472740 -66.719280
10   00614          Arecibo        Arecibo  Puerto Rico  18.456900 -66.735890
11   00616         Bajadero        Arecibo  Puerto Rico  18.420412 -66.671979
12   00617      Barceloneta    Barceloneta  Puerto Rico  18.445147 -66.559696
13   00622         Boqueron      Cabo Rojo  Puerto Rico  17.991245 -67.153993
14   00623        Cabo Rojo      Cabo Rojo  Puerto Rico  18.083361 -67.153897
15   00624         Penuelas       Penuelas  Puerto Rico  18.064919 -66.716683
16   00627            Camuy          Camuy  Puerto Rico  18.412600 -66.863926
17   00631         Castaner          Lares  Puerto Rico  18.190607 -66.832041
18   00636          Rosario     San German  Puerto Rico  18.162130 -67.077930
19   00637    Sabana Grande  Sabana Grande  Puerto Rico  18.076713 -66.947389
20   00638           Ciales         Ciales  Puerto Rico  18.295913 -66.515588
21   00641           Utuado         Utuado  Puerto Rico  18.263085 -66.712985
22   00646           Dorado         Dorado  Puerto Rico  18.433150 -66.285875
23   00647         Ensenada        Guanica  Puerto Rico  17.963613 -66.947127
24   00650          Florida        Florida  Puerto Rico  18.349416 -66.578079
25   00652      Garrochales        Arecibo  Puerto Rico  18.448452 -66.594127
26   00653          Guanica        Guanica  Puerto Rico  17.985033 -66.886536
27   00656       Guayanilla     Guayanilla  Puerto Rico  18.053539 -66.792931
28   00659          Hatillo        Hatillo  Puerto Rico  18.407226 -66.808999
29   00660      Hormigueros    Hormigueros  Puerto Rico  18.134695 -67.116199
30   00662          Isabela        Isabela  Puerto Rico  18.468320 -67.015781
31   00664           Jayuya         Jayuya  Puerto Rico  18.210330 -66.591616
32   00667            Lajas          Lajas  Puerto Rico  18.003422 -67.035810
33   00669            Lares          Lares  Puerto Rico  18.277102 -66.869645
34   00670       Las Marias     Las Marias  Puerto Rico  18.240187 -66.988776
35   00674           Manati         Manati  Puerto Rico  18.422908 -66.489337
36   00676             Moca           Moca  Puerto Rico  18.377637 -67.079574
37   00677           Rincon         Rincon  Puerto Rico  18.332568 -67.227022
38   00678     Quebradillas   Quebradillas  Puerto Rico  18.434099 -66.927384
39   00680         Mayaguez       Mayaguez  Puerto Rico  18.182055 -67.132502
40   00681         Mayaguez       Mayaguez  Puerto Rico  18.204310 -67.144690
41   00682         Mayaguez       Mayaguez  Puerto Rico  18.221464 -67.156039
42   00683       San German     San German  Puerto Rico  18.107800 -67.037263
43   00685    San Sebastian  San Sebastian  Puerto Rico  18.332929 -66.959689
44   00687          Morovis        Morovis  Puerto Rico  18.319026 -66.420557
45   00688     Sabana Hoyos        Arecibo  Puerto Rico  18.382264 -66.626438
46   00690      San Antonio      Aguadilla  Puerto Rico  18.495510 -67.098671
47   00692        Vega Alta      Vega Alta  Puerto Rico  18.410188 -66.336556
48   00693        Vega Baja      Vega Baja  Puerto Rico  18.423000 -66.397232
49   00694        Vega Baja      Vega Baja  Puerto Rico  18.482370 -66.391079
50   00698            Yauco  

#### Referencing latitude and longitude for creating map

In [5]:
address = '00717'

geolocator = Nominatim(user_agent="capstoneProject")
location = geolocator.geocode(address, timeout=60, exactly_one=True)
latitude = location.latitude
longitude = location.longitude
print('The decimal coordinates of 00717 are {}, {}.'.format(latitude, longitude))

The decimal coordinates of 00717 are 18.00545375, -66.6212251.


#### List of columns in the dataset

In [6]:
df.columns

Index(['ZIP', 'City Name', 'County Name', 'State Name', 'LAT', 'LNG'], dtype='object')

#### S howing map with surrounding areas

In [7]:

# create map of PR using latitude and longitude values
map_00717 = folium.Map(location=[latitude, longitude], zoom_start=12)

# add markers to map
for lat, lng, Zip in zip(df['LAT'], df['LNG'], df['ZIP']):
    label = '{}'.format(Zip)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(map_00717)  
    
map_00717

#### Four Square API Call for Neighbourhood analysis

In [8]:

CLIENT_ID = 'WLIUWGSEAK1C0RJODW42EGRJUTYXK45RBOGNRXNN3B4IVMCK'
CLIENT_SECRET = 'KIE2NWPDYGTWEFL3CJCYLHABMPNZCGNLFK3B4XCTGOBXMV0X'
VERSION = '20190301'
limit = 500 # limit of number of venues returned by Foursquare API
radius = 5000 # define radius


#### Function to find the venues near Puerto Rico Surrounding area

In [9]:

# function to repeat the exploring process to all the neighborhoods in Puerto Rico
import urllib
def getNearbyVenues(names, latitudes, longitudes, radius=1000, categoryIds=''):
    try:
        venues_list=[]
        for name, lat, lng in zip(names, latitudes, longitudes):
            #print(name)

            # create the API request URL
            url = 'https://api.foursquare.com/v2/venues/search?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, VERSION, lat, lng, radius, limit)

            if (categoryIds != ''):
                url = url + '&categoryId={}'
                url = url.format(categoryIds)

            # make the GET request
            response = requests.get(url).json()
            results = response["response"]['venues']

            # return only relevant information for each nearby venue
            for v in results:
                success = False
                try:
                    category = v['categories'][0]['name']
                    success = True
                except:
                    pass

                if success:
                    venues_list.append([(
                        name, 
                        lat, 
                        lng, 
                        v['name'], 
                        v['location']['lat'], 
                        v['location']['lng'],
                        v['categories'][0]['name']
                    )])

        nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
        nearby_venues.columns = ['Localidad', 
                  'Localidad Latitude', 
                  'Localidad Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    except:
        print(url)
        print(response)
        #print(results)
        print(nearby_venues)

    return(nearby_venues)

#### List of burger points

In [13]:
zipcode_venues_burger = getNearbyVenues(names=df['ZIP'], latitudes=df['LAT'], longitudes=df['LNG'], radius=1000,categoryIds='4bf58dd8d48988d16c941735')
venues_at_zipcode.head()


Localidad  Localidad Latitude  Localidad Longitude                 Venue  \
0     00601           18.165950           -66.723630           Burger King   
1     00605           18.436150           -67.151340            Joe Spud's   
2     00605           18.436150           -67.151340  Wendy's Aguadilla #2   
3     00613           18.472740           -66.719280   Burger King arecibo   
4     00623           18.083361           -67.153897               Wiliche   

   Venue Latitude  Venue Longitude        Venue Category  
0       18.169486       -66.726676  Fast Food Restaurant  
1       18.439296       -67.147833          Burger Joint  
2       18.443918       -67.146470          Burger Joint  
3       18.469993       -66.722496          Burger Joint  
4       18.086051       -67.145678          Burger Joint

In [14]:
zipcode_venues_burger.shape

(213, 7)

#### Function to add markers for given venues to map

In [15]:

def addToMap(df, color, existingMap):
    for lat, lng, local, venue, venueCat in zip(df['Venue Latitude'], df['Venue Longitude'], df['Localidad'], df['Venue'], df['Venue Category']):
        label = '{} ({}) - {}'.format(venue, venueCat, local)
        label = folium.Popup(label, parse_html=True)
        folium.CircleMarker(
            [lat, lng],
            radius=5,
            popup=label,
            color=color,
            fill=True,
            fill_color=color,
            fill_opacity=0.7).add_to(existingMap)

In [16]:
map_venues_zipcode = folium.Map(location=[latitude, longitude], zoom_start=12)
addToMap(venues_at_zipcode, 'red', map_venues_zipcode)
map_venues_zipcode

from pandas.io.json import json_normalize
df = pd.DataFrame.from_dict(json_normalize(xdict), orient='columns')

#### List of High schools

In [17]:
zipcode_venues_highschools = getNearbyVenues(names=df['ZIP'], latitudes=df['LAT'], longitudes=df['LNG'], radius=1000, categoryIds='4bf58dd8d48988d13d941735')
zipcode_venues_highschools.head()

Localidad  Localidad Latitude  Localidad Longitude  \
0     00601           18.165950           -66.723630   
1     00604           18.505290           -67.135900   
2     00614           18.456900           -66.735890   
3     00636           18.162130           -67.077930   
4     00637           18.076713           -66.947389   

                          Venue  Venue Latitude  Venue Longitude  \
0      Escuela José Emilio Lugo       18.162628       -66.721026   
1                  Ramey School       18.498053       -67.139784   
2       Abelardo Martinez Otero       18.465688       -66.739285   
3     Laura Mercado High School       18.165284       -67.078158   
4  Missionary Christian Academy       18.071133       -66.942162   

  Venue Category  
0    High School  
1    High School  
2    High School  
3    High School  
4    High School

In [18]:
zipcode_venues_highschools.shape

(149, 7)

#### Showing Schools in the map

In [20]:
map_zipcode_schools = folium.Map(location=[latitude, longitude], zoom_start=12)
addToMap(zipcode_venues_highschools, 'blue', map_zipcode_schools)
map_zipcode_schools

#### List of Universities

In [21]:
zipcode_venues_uni = getNearbyVenues(names=df['ZIP'], latitudes=df['LAT'], longitudes=df['LNG'], radius=1000, categoryIds='4bf58dd8d48988d1ae941735')
zipcode_venues_uni.head()

Localidad  Localidad Latitude  Localidad Longitude  \
0     00601            18.16595            -66.72363   
1     00604            18.50529            -67.13590   
2     00604            18.50529            -67.13590   
3     00613            18.47274            -66.71928   
4     00614            18.45690            -66.73589   

                                    Venue  Venue Latitude  Venue Longitude  \
0                         Esc Jose E Lugo       18.168703       -66.722083   
1                           UPR Aguadilla       18.499344       -67.135543   
2  Caribbean Aviation Technical Institute       18.501749       -67.140990   
3                               Resepcion       18.473582       -66.718891   
4              UNE. Universidad del Este.       18.459937       -66.743102   

  Venue Category  
0     University  
1     University  
2     University  
3     University  
4     University

In [22]:
zipcode_venues_uni.shape



(187, 7)

#### Map showing Universities

In [23]:
map_zipcode_uni = folium.Map(location=[latitude, longitude], zoom_start=12)
addToMap(zipcode_venues_uni, 'green', map_zipcode_uni)
map_zipcode_uni


#### List Of Offices

In [24]:
zipcode_venues_office = getNearbyVenues(names=df['ZIP'], latitudes=df['LAT'], longitudes=df['LNG'], radius=1000, categoryIds='4d4b7105d754a06375d81259')
zipcode_venues_office.head()

Localidad  Localidad Latitude  Localidad Longitude  \
0     00601            18.16595            -66.72363   
1     00601            18.16595            -66.72363   
2     00601            18.16595            -66.72363   
3     00601            18.16595            -66.72363   
4     00601            18.16595            -66.72363   

                                       Venue  Venue Latitude  Venue Longitude  \
0                        Comite PPD Adjuntas       18.165085       -66.723804   
1  Tribunal de Primera Instancia de Adjuntas       18.166603       -66.724940   
2             COMICIÓN ESTATAL DE ELECCIONES       18.164359       -66.723519   
3                       Funeraria Del Carmen       18.162893       -66.725784   
4               Laboratorio Clinico Adjuntas       18.163314       -66.723996   

        Venue Category  
0  Government Building  
1           Courthouse  
2         Voting Booth  
3         Funeral Home  
4               Office

In [25]:
zipcode_venues_office.shape

(3812, 7)

#### Offices in MAP

In [26]:
map_zipcode_office = folium.Map(location=[latitude, longitude], zoom_start=12)
addToMap(zipcode_venues_office, 'blue', map_zipcode_office)
map_zipcode_office

#### Adding the columns of  High schools, Universities and Offices to the data frame and aggreagte the counts of each of them .

In [27]:
def addColumn(startDf, columnTitle, dataDf):
    grouped = dataDf.groupby('Localidad').count()
    
    for n in startDf['Localidad']:
        try:
            startDf.loc[startDf['Localidad'] == n,columnTitle] = grouped.loc[n, 'Venue']
        except:
            startDf.loc[startDf['Localidad'] == n,columnTitle] = 0

In [28]:
df_data = df.copy()
df_data.rename(columns={'ZIP':'Localidad'}, inplace=True)
addColumn(df_data, 'Burger', zipcode_venues_burger)
addColumn(df_data, 'High Schools', zipcode_venues_highschools)
addColumn(df_data, 'Universities', zipcode_venues_uni)
addColumn(df_data, 'Offices', zipcode_venues_office)
df_data

Localidad        City Name    County Name   State Name        LAT  \
0       00601         Adjuntas       Adjuntas  Puerto Rico  18.165950   
1       00602           Aguada         Aguada  Puerto Rico  18.361945   
2       00603        Aguadilla      Aguadilla  Puerto Rico  18.455183   
3       00604        Aguadilla      Aguadilla  Puerto Rico  18.505290   
4       00605        Aguadilla      Aguadilla  Puerto Rico  18.436150   
5       00606          Maricao        Maricao  Puerto Rico  18.158345   
6       00610           Anasco         Anasco  Puerto Rico  18.295366   
7       00611          Angeles         Utuado  Puerto Rico  18.287720   
8       00612          Arecibo        Arecibo  Puerto Rico  18.402253   
9       00613          Arecibo        Arecibo  Puerto Rico  18.472740   
10      00614          Arecibo        Arecibo  Puerto Rico  18.456900   
11      00616         Bajadero        Arecibo  Puerto Rico  18.420412   
12      00617      Barceloneta    Barceloneta  Puerto Rico  18.445147   
13      00622         Boqueron      Cabo Rojo  Puerto Rico  17.991245   
14      00623        Cabo Rojo      Cabo Rojo  Puerto Rico  18.083361   
15      00624         Penuelas       Penuelas  Puerto Rico  18.064919   
16      00627            Camuy          Camuy  Puerto Rico  18.412600   
17      00631         Castaner          Lares  Puerto Rico  18.190607   
18      00636          Rosario     San German  Puerto Rico  18.162130   
19      00637    Sabana Grande  Sabana Grande  Puerto Rico  18.076713   
20      00638           Ciales         Ciales  Puerto Rico  18.295913   
21      00641           Utuado         Utuado  Puerto Rico  18.263085   
22      00646           Dorado         Dorado  Puerto Rico  18.433150   
23      00647         Ensenada        Guanica  Puerto Rico  17.963613   
24      00650          Florida        Florida  Puerto Rico  18.349416   
25      00652      Garrochales        Arecibo  Puerto Rico  18.448452   
26      00653          Guanica        Guanica  Puerto Rico  17.985033   
27      00656       Guayanilla     Guayanilla  Puerto Rico  18.053539   
28      00659          Hatillo        Hatillo  Puerto Rico  18.407226   
29      00660      Hormigueros    Hormigueros  Puerto Rico  18.134695   
30      00662          Isabela        Isabela  Puerto Rico  18.468320   
31      00664           Jayuya         Jayuya  Puerto Rico  18.210330   
32      00667            Lajas          Lajas  Puerto Rico  18.003422   
33      00669            Lares          Lares  Puerto Rico  18.277102   
34      00670       Las Marias     Las Marias  Puerto Rico  18.240187   
35      00674           Manati         Manati  Puerto Rico  18.422908   
36      00676             Moca           Moca  Puerto Rico  18.377637   
37      00677           Rincon         Rincon  Puerto Rico  18.332568   
38      00678     Quebradillas   Quebradillas  Puerto Rico  18.434099   
39      00680         Mayaguez       Mayaguez  Puerto Rico  18.182055   
40      00681         Mayaguez       Mayaguez  Puerto Rico  18.204310   
41      00682         Mayaguez       Mayaguez  Puerto Rico  18.221464   
42      00683       San German     San German  Puerto Rico  18.107800   
43      00685    San Sebastian  San Sebastian  Puerto Rico  18.332929   
44      00687          Morovis        Morovis  Puerto Rico  18.319026   
45      00688     Sabana Hoyos        Arecibo  Puerto Rico  18.382264   
46      00690      San Antonio      Aguadilla  Puerto Rico  18.495510   
47      00692        Vega Alta      Vega Alta  Puerto Rico  18.410188   
48      00693        Vega Baja      Vega Baja  Puerto Rico  18.423000   
49      00694        Vega Baja      Vega Baja  Puerto Rico  18.482370   
50      00698            Yauco          Yauco  Puerto Rico  18.064848   
51      00703     Aguas Buenas   Aguas Buenas  Puerto Rico  18.248401   
52      00704          Aguirre        Salinas  Puerto Rico  17.965770   
53      00705         Aibonito       Aibonito  Puerto Rico  18

#### In order to find the score of each location we add appropriate weights to the locations based on the venues 

In [29]:
# negative weight, to open a burger point we want to avoid concurrence as much as possible
weight_burger = -1

#  because high school students are good customers
weight_schools = 1

#  university students are good customers so given positive
weight_uni = 2

#  employees are even better customers so more weight
weight_offices = 3

#### Applying weights to find the score to find suitable location

In [30]:
df_weighted = df_data[['Localidad']].copy()


In [31]:
df_weighted['Score'] = df_data['Burger'] * weight_burger + df_data['High Schools'] * weight_schools + df_data['Universities'] * weight_uni + df_data['Offices'] * weight_offices
df_weighted = df_weighted.sort_values(by=['Score'], ascending=False)
df_weighted

Localidad  Score
128     00925  187.0
134     00931  176.0
133     00930  175.0
139     00937  168.0
148     00955  168.0
120     00917  167.0
137     00935  166.0
140     00939  166.0
141     00940  166.0
163     00975  166.0
58      00717  165.0
122     00919  165.0
131     00928  161.0
121     00918  160.0
152     00959  158.0
40      00681  157.0
126     00923  157.0
112     00909  157.0
130     00927  156.0
138     00936  156.0
115     00912  154.0
159     00968  153.0
113     00910  152.0
136     00934  150.0
169     00982  149.0
76      00737  149.0
111     00908  148.0
114     00911  148.0
104     00792  147.0
125     00922  146.0
154     00961  145.0
116     00913  145.0
109     00906  145.0
108     00902  144.0
135     00933  144.0
107     00901  144.0
124     00921  143.0
123     00920  143.0
171     00984  143.0
127     00924  142.0
4       00605  142.0
132     00929  141.0
119     00916  141.0
150     00957  141.0
110     00907  140.0
170     00983  140.0
153     00960  139.0
157     00965  139.0
9       00613  139.0
64      00725  138.0
101     00785  138.0
158     00966  137.0
160     00969  137.0
65      00726  137.0
168     00981  137.0
173     00986  137.0
175     00988  137.0
161     00970  136.0
35      00674  134.0
106     00795  123.0
165     00977  120.0
10      00614  117.0
91      00771  116.0
14      00623  115.0
117     00914  114.0
118     00915  113.0
167     00979  110.0
147     00954  109.0
78      00739  104.0
73      00734   97.0
72      00733   93.0
0       00601   92.0
57      00716   88.0
145     00952   88.0
47      00692   78.0
3       00604   74.0
103     00791   69.0
155     00962   61.0
30      00662   58.0
166     00978   57.0
46      00690   54.0
95      00777   53.0
41      00682   44.0
15      00624   39.0
62      00721   38.0
156     00963   36.0
22      00646   36.0
39      00680   34.0
98      00782   32.0
96      00778   29.0
67      00728   28.0
75      00736   28.0
29      00660   27.0
79      00740   27.0
31      00664   25.0
21      00641   24.0
12      00617   24.0
71      00732   22.0
80      00741   21.0
52      00704   21.0
69      00730   18.0
6       00610   15.0
36      00676   15.0
164     00976   14.0
56      00715   12.0
53      00705   12.0
45      00688   12.0
48      00693   12.0
129     00926   12.0
149     00956   12.0
19      00637   10.0
68      00729   10.0
34      00670   10.0
144     00951    9.0
18      00636    7.0
66      00727    6.0
44      00687    6.0
42      00683    6.0
60      00719    4.0
146     00953    3.0
142     00949    3.0
143     00950    3.0
151     00958    3.0
2       00603    3.0
7       00611    3.0
43      00685    3.0
88      00766    3.0
87      00765    3.0
54      00707    3.0
99      00783    3.0
59      00718    3.0
102     00786    3.0
83      00745    3.0
84      00751    3.0
162     00971    0.0
89      00767    0.0
1       00602    0.0
17      00631    0.0
16      00627    0.0
86      00757    0.0
13      00622    0.0
11      00616    0.0
85      00754    0.0
20      00638    0.0
8       00612    0.0
82      00744    0.0
81      00742    0.0
5       00606    0.0
77      00738    0.0
172     00985    0.0
74      00735    0.0
174     00987    0.0
90      00769    0.0
70      00731    0.0
92      00772    0.0
49      00694    0.0
38      00678    0.0
50      00698    0.0
37      00677    0.0
51      00703    0.0
33      00669    0.0
32      00667    0.0
55      00714    0.0
61      00720    0.0
28      00659    0.0
27      00656    0.0
26      00653    0.0
25      00652    0.0
105     00794    0.0
63      00723    0.0
100     00784    0.0
24      00650    0.0
23      00647    0.0
97      00780    0.0
94      00775    0.0
93      00773    0.0

#### From the results above zipcode 00925 (SAN JUAN) is the best area to open Burger shop in the state Puerto Rico because it got the best score out of all

#### Create a map showing the results. ie. burger point, schools, universities, offices

In [32]:
map_zipcode_result = folium.Map(location=[latitude, longitude], zoom_start=15)

zipcode_win = df[df['ZIP'] == '00925']

for lat, lng, local in zip(zipcode_win['LAT'], zipcode_win['LNG'], zipcode_win['ZIP']):
    label = '{}'.format(local)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='blue',
        fill_opacity=0.7).add_to(map_zipcode_result) 

addToMap(zipcode_venues_burger[zipcode_venues_burger['Localidad'] == '00925'], 'red', map_zipcode_result)
addToMap(zipcode_venues_highschools[zipcode_venues_highschools['Localidad'] == '00925'], 'green', map_zipcode_result)
addToMap(zipcode_venues_uni[zipcode_venues_uni['Localidad'] == '00925'], 'blue', map_zipcode_result)
addToMap(zipcode_venues_office[zipcode_venues_office['Localidad'] == '00925'], 'fuchsia', map_zipcode_result)

map_zipcode_result

#### Details of this 00925 are

In [33]:

import zipcodes
zipcodes.matching('00925')

[{'zip_code': '00925',
  'zip_code_type': 'STANDARD',
  'city': 'SAN JUAN',
  'state': 'PR',
  'lat': 18.4,
  'long': -66.06,
  'world_region': 'NA',
  'country': 'US',
  'active': True}]

#### We will examine how many burger pointes are there at this location now serving how many schools, universities and offices at thi location

#### There are 3 Burger points now 

In [34]:
venues_at_zipcode[venues_at_zipcode['Localidad']=='00925'].shape

(3, 7)

#### There are 18 schools nearby

In [35]:
zipcode_venues_uni[zipcode_venues_uni['Localidad']=='00925'].shape

(18, 7)

#### There are 50 Universities near by.

In [37]:
zipcode_venues_office[zipcode_venues_office['Localidad']=='00925'].shape

(50, 7)

## Conclusion:
We can start a new burger point at SAN JUAN (00925) at this location since we have potential customers to serve and earn profits
